<a href="https://colab.research.google.com/github/cappelchi/calcio_notebooks/blob/main/draft/football_live_validation_multiclass_report_11.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Делает отчет по предиктам в мультиклассе и визуализрует результат

### Project config

In [ ]:
try:
    import neptune.new as neptune
except:
    !pip install neptune-client >> None
    import neptune.new as neptune
#from neptune.new.integrations.tensorflow_keras import NeptuneCallback
def get_credential(frmwork = 'neptune_team'):
    with open('credential.txt', 'r') as container:
        for line in container:
            if frmwork in line:
                login, psw = line.split(' ')[1], line.split(' ')[2].split('\n')[0]
                return login, psw

/usr/local/lib/python3.10/dist-packages/neptune/internal/backends/hosted_client.py:50: NeptuneDeprecationWarning: The 'neptune-client' package has been deprecated and will be removed in the future. Install the 'neptune' package instead. For more, see https://docs.neptune.ai/setup/upgrading/
  from neptune.version import version as neptune_client_version
<ipython-input-1-94b4efcbc4c0>:5: NeptuneDeprecationWarning: You're importing the Neptune client library via the deprecated `neptune.new` module, which will be removed in a future release. Import directly from `neptune` instead.
  import neptune.new as neptune


In [ ]:
#@title Set API key for neptune.ai
set_api = True #@param {type:"boolean"}
if set_api:
    username, api_key = get_credential()

### Installations

In [ ]:
!pip install catboost >> None

### Downloads

In [ ]:
!wget -q -O ./data.rar https://getfile.dokpub.com/yandex/get/https://disk.yandex.ru/d/IWvldpeoQcAh5w
!mkdir -p ./Result2
!unrar e ./data.rar ./Result2/

In [ ]:
#!wget -q -O ./Result2.rar https://getfile.dokpub.com/yandex/get/https://disk.yandex.ru/d/MwzjeVAGOZwJaw
!wget -q -O ./Prem.rar https://getfile.dokpub.com/yandex/get/https://disk.yandex.ru/d/oTq97titK56Y2A
!mkdir -p ./Prem
!unrar e ./Prem.rar ./Prem/

In [ ]:
!wget -q -O ./Index.rar https://getfile.dokpub.com/yandex/get/https://disk.yandex.ru/d/rVBc3eq2SG8Ppw
!mkdir -p ./Index
!unrar e ./Index.rar ./Index/


UNRAR 5.61 beta 1 freeware      Copyright (c) 1993-2018 Alexander Roshal


Extracting from ./Index.rar

Extracting  ./Index/20230110.csv                                           0%  OK 
Extracting  ./Index/20230109.csv                                           0%  OK 
Extracting  ./Index/20230108.csv                                           1%  OK 
Extracting  ./Index/20230107.csv                                           2%  OK 
Extracting  ./Index/20230106.csv                                           3%  OK 
Extracting  ./Index/20230105.csv                                           3%  OK 
Extracting  ./Index/20230104.csv                                           3%  OK 
Extracting  ./Index/20230103.csv                                           4%  OK 
Extracting  ./Index/20230102.csv                                           4%  OK 
Extracting  ./Index/20230101.csv                                   

### Imports

In [ ]:
import pandas as pd
import numpy as np
pd.options.display.max_columns = 100
pd.options.display.max_rows = 100
print(pd.__version__)
print(np.__version__)

1.5.3
1.22.4


In [ ]:
np.iinfo(np.int8).max, np.iinfo(np.int16).max, np.iinfo(np.int32).max

(127, 32767, 2147483647)

In [ ]:
np.finfo(np.float16).precision, np.finfo(np.float32).precision, np.finfo(np.float64).precision

(3, 6, 15)

In [ ]:
import os, psutil, time
from glob import glob
from tqdm import tqdm
import functools

In [ ]:
from catboost import CatBoost

### Code

#####Functions

In [ ]:
def define_files_list(date_start:str, folder:str, date_end = '') -> list:
    '''
    data_start, data_end
    folder: ./folder/
    '''
    if date_end == '':
        return sorted(
            [file 
            for file in glob(folder + '*') 
            if int(file.split('/')[-1].split('.csv')[0]) >= int(date_start)]
            )
    else:
        return sorted(
            [file 
            for file in glob(folder + '*') 
            if int(file.split('/')[-1].split('.csv')[0]) >= int(date_start) & \
                int(file.split('/')[-1].split('.csv')[0]) <= int(date_end)]
            )

In [ ]:
def create_id_dict(date_start, folder, cols, date_end = '') -> dict:
    '''
    '''
    return pd.concat(map(
        functools.partial(
            pd.read_csv, sep=';', usecols =  cols
                            ),
                    define_files_list(date_start, folder, date_end = date_end)
                    ), ignore_index=True).drop_duplicates(subset = ['Id'], keep = 'last').set_index('Id').to_dict(orient = 'index')

In [ ]:
def transform_dataset(data_df:pd.DataFrame, remain = []):
    new_match_vector = data_df['Id'] != data_df['Id'].shift(1)
    # трансформируем минуты
    data_df['min_norm'] = data_df['Minute'].astype(np.float32) / 50
    print('1. Минуты посчитаны...')
    # трансформируем голы
    data_df[data_df['Score1'].isna() & new_match_vector] = 0
    data_df['Score1_norm'] = data_df['Score1'].fillna(method = 'ffill').astype(np.float32) / 4
    data_df.loc[data_df['Score1'] > 3, ['Score1_norm']] = 1.0
    data_df[data_df['Score2'].isna() & new_match_vector] = 0
    data_df['Score2_norm'] = data_df['Score2'].fillna(method = 'ffill').astype(np.float32) / 4
    data_df.loc[data_df['Score2'] > 3, ['Score2_norm']] = 1.0

    data_df['Score_diff'] = data_df['Score1'].astype(np.int16) - data_df['Score2'].astype(np.int16)
    data_df.loc[data_df['Score_diff'] < -4, ['Score_diff']] = -4
    data_df.loc[data_df['Score_diff'] > 4, ['Score_diff']] = 4
    data_df[[f'Score_cat_{n}' for n in range(1, 10)]] = pd.get_dummies(data_df['Score_diff']).values
    data_df['Score_diff'] = data_df['Score_diff'].astype(np.float32) / np.float32(4.0)
    if 'Score1' not in remain:
        data_df = data_df.drop(['Score1', 'Score2'], axis = 1)
    print('2. Голы посчитаны...')
    #трансформируем атаки
    data_df['A1_scaled'] = data_df['A1'].astype(np.float32) / 75
    data_df.loc[data_df['A1'] >= 60, ['A1_scaled']] = (60 + (data_df['A1'] - 60) / 4) / 75
    data_df['A2_scaled'] = data_df['A2'].astype(np.float32) / 75
    data_df.loc[data_df['A2'] >= 60, ['A2_scaled']] = (60 + (data_df['A2'] - 60) / 4) / 75
    # атаки в минуту
    data_df['A1perMIN'] = data_df['A1'].astype(np.float32) / data_df['Minute'].astype(np.float32)
    data_df.loc[data_df['A1perMIN'] > 4, ['A1perMIN']] = np.float32(4.0)
    data_df['A2perMIN'] = data_df['A2'].astype(np.float32) / data_df['Minute'].astype(np.float32)
    data_df.loc[data_df['A2perMIN'] > 4, ['A2perMIN']] = np.float32(4.0)
    # динамика атак
    new_match_vector5 = data_df['Id'] != data_df['Id'].shift(5)
    data_df['A1relativ'] = data_df['A1'].astype(np.float32) - data_df['A1'].shift(5).astype(np.float32)
    data_df.loc[new_match_vector5, ['A1relativ']] = np.float32(0.0)
    data_df['A1relativ'] = data_df['A1relativ'].fillna(0)
    data_df.loc[data_df['A1relativ'] > 15, ['A1relativ']] = np.float32(15.)
    data_df['A2relativ'] = data_df['A2'].astype(np.float32) - data_df['A2'].shift(5).astype(np.float32)
    data_df.loc[new_match_vector5, ['A2relativ']] =  np.float32(0.0)
    data_df['A2relativ'] = data_df['A2relativ'].fillna(0)
    data_df.loc[data_df['A2relativ'] > 15, ['A2relativ']] = np.float32(15.)
    if 'A1' not in remain:
        data_df = data_df.drop(['A1', 'A2'], axis = 1)
    print('3. Атаки посчитаны...')
    # трансформируем опасные атаки
    data_df['DA1_scaled'] = data_df['DA1'].astype(np.float32) / 50
    data_df.loc[data_df['DA1'] >= 40, ['DA1_scaled']] = (80 + (data_df['DA1'] - 40) / 3) / 100
    data_df['DA2_scaled'] = data_df['DA2'].astype(np.float32) / 50
    data_df.loc[data_df['DA2'] >= 40, ['DA2_scaled']] = (80 + (data_df['DA2'] - 40) / 3) / 100
    # опасные атаки в минуту    
    data_df['DA1perMIN'] = data_df['DA1'].astype(np.float32) / data_df['Minute'].astype(np.float32)
    data_df.loc[data_df['DA1perMIN'] > 3, ['DA1perMIN']] = np.float32(3.0)
    data_df['DA2perMIN'] = data_df['DA2'].astype(np.float32) / data_df['Minute'].astype(np.float32)
    data_df.loc[data_df['DA2perMIN'] > 3, ['DA2perMIN']] = np.float32(3.0)
    # динамика опасных атак
    data_df['DA1relativ'] = data_df['DA1'].astype(np.float32) - data_df['DA1'].shift(5).astype(np.float32)
    data_df.loc[new_match_vector5, ['DA1relativ']] = np.float32(0.0)
    data_df['DA1relativ'] = data_df['DA1relativ'].fillna(0)
    data_df.loc[data_df['DA1relativ'] > 10, ['DA1relativ']] = np.float32(10.)
    data_df['DA2relativ'] = data_df['DA2'].astype(np.float32) - data_df['DA2'].shift(5).astype(np.float32)
    data_df.loc[new_match_vector5, ['DA2relativ']] = np.float32(0.0)
    data_df['DA2relativ'] = data_df['DA2relativ'].fillna(0)
    data_df.loc[data_df['DA2relativ'] > 10, ['DA2relativ']] = np.float32(10.)
    if 'DA1' not in remain:
        data_df = data_df.drop(['DA1', 'DA2'], axis = 1)
    if 'Minute' not in remain:
        data_df = data_df.drop(['Minute'], axis = 1)
    print('4. Опасные атаки посчитаны...')
    # трансформируем владение мячом
    data_df[data_df['Pos1'].isna() & new_match_vector] = 0
    data_df['Pos1_cleaned'] = data_df['Pos1'].fillna(method = 'ffill').astype(np.float32) /  np.float32(100.0)
    data_df.loc[data_df['Pos1_cleaned'] < 0.2, ['Pos1_cleaned']] = np.float32(0.2)
    data_df.loc[data_df['Pos1_cleaned'] > 0.8, ['Pos1_cleaned']] = np.float32(0.8)
    data_df[data_df['Pos2'].isna() & new_match_vector] = 0
    data_df['Pos2_cleaned'] = data_df['Pos2'].fillna(method = 'ffill').astype(np.float32) /  np.float32(100.0)
    data_df.loc[data_df['Pos2_cleaned'] < 0.2, ['Pos2_cleaned']] = np.float32(0.2)
    data_df.loc[data_df['Pos2_cleaned'] > 0.8, ['Pos2_cleaned']] = np.float32(0.8)
    if 'Pos1' not in remain:
        data_df = data_df.drop(['Pos1', 'Pos2'], axis = 1)
    print('5. Владение мячом посчитпно...')
    # трансформируем удары
    data_df[data_df['Off1'].isna() & new_match_vector] = 0
    data_df['Off1_norm'] = data_df['Off1'].fillna(method = 'ffill').astype(np.float32) / np.float32(10.0)
    data_df.loc[data_df['Off1_norm'] > 1.0, ['Off1_norm']] = np.float32(1.0)
    data_df[data_df['Off2'].isna() & new_match_vector] = 0
    data_df['Off2_norm'] = data_df['Off2'].fillna(method = 'ffill').astype(np.float32) / np.float32(10.0)
    data_df.loc[data_df['Off2_norm'] > 1.0, ['Off2_norm']] = np.float32(1.0)
    if 'Off1' not in remain:
        data_df = data_df.drop(['Off1', 'Off2'], axis = 1)
    print('6. Удары посчитаны...')
    # трансформируем удары в створ
    data_df[data_df['On1'].isna() & new_match_vector] = 0
    data_df['On1_norm'] = data_df['On1'].fillna(method = 'ffill').astype(np.float32) / np.float32(5.0)
    data_df.loc[data_df['On1_norm'] > 1.0, ['On1_norm']] = np.float32(1.0)
    data_df[data_df['On2'].isna() & new_match_vector] = 0
    data_df['On2_norm'] = data_df['On2'].fillna(method = 'ffill').astype(np.float32) / np.float32(5.0)
    data_df.loc[data_df['On2_norm'] > 1.0, ['On2_norm']] = np.float32(1.0)
    if 'On1' not in remain:
        data_df = data_df.drop(['On1', 'On2'], axis = 1)    
    print('7. Удары в створ посчитаны...')
    # трансформируем желтые карточки
    data_df[data_df['YC1'].isna() & new_match_vector] = 0
    data_df['YC1_transformed'] = data_df['YC1'].fillna(0).astype(np.float32) / np.float32(2.0)
    data_df.loc[data_df['YC1_transformed'] > 1.0, ['YC1_transformed']] = np.float32(1.0)
    data_df[data_df['YC2'].isna() & new_match_vector] = 0
    data_df['YC2_transformed'] = data_df['YC2'].fillna(0).astype(np.float32) / np.float32(2.0)
    data_df.loc[data_df['YC2_transformed'] > 1.0, ['YC2_transformed']] = np.float32(1.0)
    if 'YC1' not in remain:
        data_df = data_df.drop(['YC1', 'YC2'], axis = 1)
    print('8. Жёлтые карточки посчитаны...')
    # трансформируем красные карточки
    data_df[data_df['RC1'].isna() & new_match_vector] = 0
    data_df['RC1_transformed'] = data_df['RC1'].fillna(0).astype(np.int8)
    data_df.loc[data_df['RC1_transformed'] > 1, ['RC1_transformed']] = np.int8(1)
    data_df[data_df['RC2'].isna() & new_match_vector] = 0
    data_df['RC2_transformed'] = data_df['RC2'].fillna(0).astype(np.int8)
    data_df.loc[data_df['RC2_transformed'] > 1, ['RC2_transformed']] = np.int8(1)
    if 'RC1' not in remain:
        data_df = data_df.drop(['RC1', 'RC2'], axis = 1)
    print('9. Красные карточки посчитаны...')
    # трансформируем замены
    data_df[data_df['Sub1'].isna() & new_match_vector] = 0
    data_df['Sub1_transformed'] = data_df['Sub1'].fillna(0).astype(np.int8)
    data_df.loc[data_df['Sub1_transformed'] > 1, ['Sub1_transformed']] = np.int8(1)
    data_df[data_df['Sub2'].isna() & new_match_vector] = 0
    data_df['Sub2_transformed'] = data_df['Sub2'].fillna(0).astype(np.int8)
    data_df.loc[data_df['Sub2_transformed'] > 1, ['Sub2_transformed']] = np.int8(1)
    if 'Sub1' not in remain:
        data_df = data_df.drop(['Sub1', 'Sub2'], axis = 1)
    print('10. Замены посчитаны...')
    # трансформируем угловык
    data_df[data_df['Cor1'].isna() & new_match_vector] = 0
    data_df['Cor1_transformed'] = data_df['Cor1'].fillna(0).astype(np.float32) / np.float32(6.0)
    data_df.loc[data_df['Cor1_transformed'] > 1.0, ['Cor1_transformed']] = np.float32(1.0)
    data_df[data_df['Cor2'].isna() & new_match_vector] = 0
    data_df['Cor2_transformed'] = data_df['Cor2'].fillna(0).astype(np.float32) / np.float32(6.0)
    data_df.loc[data_df['Cor2_transformed'] > 1.0, ['Cor2_transformed']] = np.float32(1.0)
    if 'Cor1' not in remain:
        data_df = data_df.drop(['Cor1', 'Cor2'], axis = 1)
    print('11. Угловые посчитаны...')
    # трансформируем линию
    data_df['P1_transformed'] = np.log(data_df['P1'], dtype = np.float32) / 2
    data_df['P2_transformed'] = np.log(data_df['P2'], dtype = np.float32) / 2
    if 'P1' not in remain:
        data_df = data_df.drop(['P1', 'P2'], axis = 1)
    print('12. Линии посчитаны...')
    if 'Pen1' not in remain:
        data_df = data_df.drop(['Pen1', 'Pen2'], axis = 1)
    if 'Active' not in remain:
        data_df = data_df.drop(['Active'], axis = 1)
    return data_df

#### Predefine data

In [ ]:
import datetime
data_types_dict = {
    'Id':np.int32, 
    'StatTime':str, 
    'Minute':np.int8, 
    'Active': np.int8, 'Score1':np.int8, 'Score2':np.int8,
    'A1':np.int16, 'A2':np.int16, 'DA1':np.int16, 'DA2':np.int16, 'Pos1':np.float32, 'Pos2':np.float32,
    'Off1':np.int8, 'Off2':np.int8, 'On1':np.int8, 'On2':np.int8, 'YC1':np.int8, 'YC2':np.int8,
    'RC1':np.int8, 'RC2':np.int8, 'Sub1':np.int8, 'Sub2':np.int8, 'Pen1':np.int8, 'Pen2':np.int8,
    'Cor1':np.int8, 'Cor2':np.int8, 'Period':np.int8, 
    'D':np.datetime64,
    'I':np.int32, 'Active.1':np.int8, 
    'Time':np.datetime64, 
    'Minute.1':np.int8, 
    'RawTime':np.datetime64, 
    'Score1.1':np.int8, 'Score2.1':np.int8, 'Period.1':np.int8, 
    'W1':np.float16, 'WX':np.float16, 'W2':np.float16, 'X1':np.float16, 'X2':np.float16, 'W12':np.float16, 'TotalValue':np.float16, 
    'Over':np.float16, 'Under':np.float16, 'Hand1Value':np.float16, 'H1':np.float16, 'H2':np.float16 
}

In [ ]:
k_cols = [
    'W1', 'WX', 'W2', 'X1', 'X2', 'W12', 'TotalValue' ,'Over',
    'Under', 'Hand1Value', 'H1', 'H2' 
]

In [ ]:
drop_cols = [
    #'StatTime', 
    'Comment', 'D', 'I', 'Time', 'Minute.1', 'RawTime',
    'Score1.1', 'Score2.1', 'Period.1', 'Period', 'Periods', 'Serve'
]

#### Load Parameters

In [ ]:
info_cols = ['Id', 'Result1', 'Result2']
prem_cols = ['Id', 'P1', 'PX', 'P2']
res_cols = [cols for cols in data_types_dict if cols not in drop_cols]

info_folder = './Index/'
prem_folder = './Prem/'
data_folder = './Result2/'

In [ ]:
### собрать датасет с даты:
year_start = '2023'
month_start = '01'
day_start = '01'
### до даты
year_end = ''
month_end = ''
day_end = ''
date_start = year_start + month_start + day_start
date_end = year_end + month_end + day_end

#### Create DataFrame

In [ ]:
info_dict = create_id_dict(date_start, info_folder, info_cols)
prem_dict = create_id_dict(date_start, prem_folder, prem_cols)
if len(prem_dict) != len(info_dict):
    print('Нет в info: ', set(prem_dict) - set(info_dict))
    print('Нет в prem: ', set(info_dict) - set(prem_dict))

In [ ]:
files_list =['./Result2/' + str(id) + '.csv' 
    for id in set(info_dict)
    if os.path.exists('./Result2/' + str(id) + '.csv')]

In [ ]:
time_point1 = time.time()
data_df = pd.concat(map(functools.partial(
    pd.read_csv, 
    sep = ';',
    #parse_dates = ['StatTime'],
    usecols = res_cols
                                    ), files_list), ignore_index=True)
time_point2 = time.time()
print(f'create dataframe: {time_point2 - time_point1} sec.')
#---------------
process = psutil.Process(os.getpid())
print(round(process.memory_info().rss / 1024 ** 3, 2), 'GiB')  # in bytes 
#---------------  

data_df[k_cols] = data_df[k_cols].fillna(0).values # Заполняем пропущенные лайв кэфы 1
new_match_vector = data_df['Id'] != data_df['Id'].shift(1) # Отмечаем переходы между матчами в колонуах
data_cols = list(set(res_cols) - set(k_cols)) # Отбирвем колонки для заполнения пропусков метдом ffill
for col in data_cols:
    data_df.loc[data_df[col].isna() & new_match_vector, col] = 0 # Сами переходы с пропусками заполняем 0
data_df = data_df.fillna(method = 'ffill')
################ Записываем файл с временными метками и сбрасываем время матчей
#(data_df['Id'].astype(str) + ':' + data_df['StatTime'].astype(str).str.split(
#        ' ', expand=True)[0]
#        ).drop_duplicates().str.split(':', expand = True).rename(
#                                                columns = {0:'Id', 1:'StatTime'}
#                                                            ).to_csv('./time.csv', index = False)
#data_df = data_df.drop(['StatTime'], axis = 1)
############################################### Присоединяем результаты и кэфы
data_df[['Result1', 'Result2']] = [
    [info_dict[id]['Result1'], info_dict[id]['Result2']] 
    for id in tqdm(data_df['Id'].values, total = len(data_df))
    ]
data_df[['P1', 'PX', 'P2']] = [
    [prem_dict[id]['P1'], prem_dict[id]['PX'], prem_dict[id]['P2']] 
    for id in tqdm(data_df['Id'].values, total = len(data_df))
    ]

print('\n')
#---------------
process = psutil.Process(os.getpid())
print(round(process.memory_info().rss / 1024 ** 3, 2), 'GiB')  # in bytes 
#---------------  

create dataframe: 137.07224249839783 sec.
1.49 GiB


100%|██████████| 1224315/1224315 [00:02<00:00, 462728.20it/s]




1.45 GiB


In [ ]:
data_df.loc[new_match_vector & (data_df['P1'].isna()), ['P1']] = data_df['W1'][new_match_vector & (data_df['P1'].isna())]
data_df.loc[new_match_vector & (data_df['P2'].isna()), ['P2']] = data_df['W2'][new_match_vector & (data_df['P2'].isna())]
data_df.loc[new_match_vector & (data_df['PX'].isna()), ['PX']] = data_df['WX'][new_match_vector & (data_df['PX'].isna())]
data_df['P1'] = data_df['P1'].fillna(method = 'ffill').values
data_df['PX'] = data_df['PX'].fillna(method = 'ffill').values
data_df['P2'] = data_df['P2'].fillna(method = 'ffill').values

In [ ]:
data_df = transform_dataset(data_df, #) 
    remain = ['StatTime', 'Minute', 'Score1', 'Score2', 'Result1', 'Result2', 'P1', 'PX', 'P2'])

1. Минуты посчитаны...
2. Голы посчитаны...
3. Атаки посчитаны...
4. Опасные атаки посчитаны...
5. Владение мячом посчитпно...
6. Удары посчитаны...
7. Удары в створ посчитаны...
8. Жёлтые карточки посчитаны...
9. Красные карточки посчитаны...
10. Замены посчитаны...
11. Угловые посчитаны...
12. Линии посчитаны...


/usr/local/lib/python3.10/dist-packages/pandas/core/arraylike.py:402: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/usr/local/lib/python3.10/dist-packages/pandas/core/arraylike.py:402: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


In [ ]:
# Из-за того что некоторые кэфы были пропущены, и заменены на нули в препроцессинге на их месте появились inf, удаляем
print('P1 -inf & P2 -inf: ', (data_df['P1_transformed'] == -np.inf).sum(), (data_df['P2_transformed'] == -np.inf).sum())

#data_df = data_df[~(data_df['P1_transformed'] == -np.inf)]
#data_df = data_df[~(data_df['P2_transformed'] == -np.inf)]


P1 -inf & P2 -inf:  1054 1054


In [ ]:
#Там где забито болше внутри матча чем в итоге, пока не удаляем
print('Score-Result error 1&2: ', (~(data_df['Result1'] - data_df['Score1']) >= 0).sum(), (~(data_df['Result1'] - data_df['Score1']) >= 0).sum())
#data_df = data_df.loc[(data_df['Result1'] - data_df['Score1']) >= 0]
#data_df = data_df.loc[(data_df['Result2'] - data_df['Score2']) >= 0]


#---------------
process = psutil.Process(os.getpid())
print('mem usage: ', round(process.memory_info().rss / 1024 ** 3, 2), 'GiB')  # in bytes 
#---------------    

Score-Result error 1&2:  20 20
mem usage:  1.66 GiB


In [ ]:
data_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1224315 entries, 0 to 1224314
Data columns (total 64 columns):
 #   Column            Non-Null Count    Dtype  
---  ------            --------------    -----  
 0   Id                1224315 non-null  int64  
 1   StatTime          1224315 non-null  object 
 2   Minute            1224315 non-null  int64  
 3   Score1            1224315 non-null  int64  
 4   Score2            1224315 non-null  int64  
 5   Active.1          1224315 non-null  int64  
 6   W1                1224315 non-null  float64
 7   WX                1224315 non-null  float64
 8   W2                1224315 non-null  float64
 9   X1                1224315 non-null  float64
 10  X2                1224315 non-null  float64
 11  W12               1224315 non-null  float64
 12  TotalValue        1224315 non-null  float64
 13  Over              1224315 non-null  float64
 14  Under             1224315 non-null  float64
 15  Hand1Value        1224315 non-null  float64
 16  

In [ ]:
data_df.describe()

Id        Minute        Score1        Score2      Active.1  \
count  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06   
mean   5.985597e+06  2.292452e+01  2.984207e-01  2.399881e-01  8.738805e-01   
std    4.262606e+05  1.296832e+01  5.944602e-01  5.271921e-01  3.319841e-01   
min    4.975839e+06  1.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
25%    5.539263e+06  1.200000e+01  0.000000e+00  0.000000e+00  1.000000e+00   
50%    6.140507e+06  2.300000e+01  0.000000e+00  0.000000e+00  1.000000e+00   
75%    6.320661e+06  3.400000e+01  0.000000e+00  0.000000e+00  1.000000e+00   
max    6.536463e+06  4.500000e+01  8.000000e+00  6.000000e+00  1.000000e+00   

                 W1            WX            W2            X1            X2  \
count  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06   
mean   3.043034e+00  3.607426e+00  4.612268e+00  1.328726e+00  1.769314e+00   
std    4.178973e+00  2.543880e+00  5.887356e+00  1.284327e+00  1.670713e+00   
min    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
25%    1.300000e+00  2.780000e+00  1.570000e+00  1.022000e+00  1.104000e+00   
50%    2.050000e+00  3.320000e+00  2.890000e+00  1.222000e+00  1.460000e+00   
75%    3.140000e+00  4.150000e+00  5.150000e+00  1.533000e+00  2.050000e+00   
max    6.900000e+01  2.600000e+01  1.260000e+02  1.850000e+01  1.850000e+01   

                W12    TotalValue          Over         Under    Hand1Value  \
count  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06   
mean   1.057339e+00  2.352563e+00  1.706362e+00  1.684186e+00 -2.538134e-01   
std    4.790495e-01  1.254568e+00  6.230953e-01  6.114745e-01  1.185541e+00   
min    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00 -1.100000e+01   
25%    1.097000e+00  1.500000e+00  1.740000e+00  1.720000e+00 -1.000000e+00   
50%    1.240000e+00  2.500000e+00  1.880000e+00  1.850000e+00  0.000000e+00   
75%    1.330000e+00  3.000000e+00  2.030000e+00  2.000000e+00  0.000000e+00   
max    2.130000e+00  1.200000e+01  1.050000e+01  3.100000e+00  1.050000e+01   

                 H1            H2       Result1       Result2            P1  \
count  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06   
mean   1.737579e+00  1.743968e+00  1.532735e+00  1.225094e+00  2.785203e+00   
std    7.104894e-01  7.129298e-01  1.402638e+00  1.249101e+00  2.865786e+00   
min    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
25%    1.580000e+00  1.590000e+00  1.000000e+00  0.000000e+00  1.650000e+00   
50%    1.830000e+00  1.840000e+00  1.000000e+00  1.000000e+00  2.150000e+00   
75%    2.110000e+00  2.120000e+00  2.000000e+00  2.000000e+00  2.900000e+00   
max    6.100000e+00  1.050000e+01  1.300000e+01  1.400000e+01  6.700000e+01   

                 PX            P2      min_norm   Score1_norm   Score2_norm  \
count  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06   
mean   4.008574e+00  4.127461e+00  4.584903e-01  7.447532e-02  5.995455e-02   
std    1.874152e+00  4.105202e+00  2.593665e-01  1.476369e-01  1.314454e-01   
min    0.000000e+00  0.000000e+00  2.000000e-02  0.000000e+00  0.000000e+00   
25%    3.200000e+00  2.250000e+00  2.400000e-01  0.000000e+00  0.000000e+00   
50%    3.500000e+00  3.100000e+00  4.600000e-01  0.000000e+00  0.000000e+00   
75%    4.000000e+00  4.500000e+00  6.800000e-01  0.000000e+00  0.000000e+00   
max    5.100000e+01  8.100000e+01  9.000000e-01  1.000000e+00  1.000000e+00   

         Score_diff   Score_cat_1   Score_cat_2   Score_cat_3   Score_cat_4  \
count  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06  1.224315e+06   
mean   1.452874e-02  6.673119e-04  3.550557e-03  1.979801e-02  1.251851e-01   
std    1.921558e-01  2.582377e-02  5.948070e-02  1.393057e-01  3.309288e-01   
min   -1.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
25%    0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00 

In [ ]:
X = data_df[data_df.columns[23:]].values
y = np.sign((data_df['Result2'] - data_df['Result1']).values) + 1
line = data_df[['W1', 'WX', 'W2']].values
#active_rows = np.ones(line.shape[0], dtype = bool) 
#active = (data_df['Active.1'] == 1).values
#active_rows = (active & (line.sum(axis = 1) > 3))

#### Download models and restore predicts

In [ ]:
# Модель для 1-ой команды
model_head = 'FOOT-LIVEMC'
model_num = 2 # Указываем номер модели
neptune_model = model_head
neptune_model_version = neptune_model + f'-{model_num}'
model_version_params = dict(
    project = 'scomesse/football',
    model = neptune_model,
    api_token = api_key,
    with_id = neptune_model_version
)
PATH_TO_MODEL = './booster.model'
model_version = neptune.init_model_version(**model_version_params)
model_version['model'].download(PATH_TO_MODEL)
params1 = model_version['team_parameters'].fetch()
model_version.stop()

https://app.neptune.ai/scomesse/football/m/FOOT-LIVEMC/v/FOOT-LIVEMC-2
Shutting down background jobs, please wait a moment...
Done!
All 0 operations synced, thanks for waiting!
Explore the metadata in the Neptune app:
https://app.neptune.ai/scomesse/football/m/FOOT-LIVEMC/v/FOOT-LIVEMC-2/metadata


In [ ]:
preds_dict = {}
booster = CatBoost()
booster.load_model('./booster.model')
preds = np.flip(booster.predict(X, prediction_type="Probability"), axis = 1) 
# здесь flip т.к предикт делали по схеме (0:away, 1:draw, 2:home), после flip'a получаем (0:home, 1:draw, 2:away)

#### Report

In [ ]:
data_df[['H_prob', 'D_prob', 'A_prob']] = preds

In [ ]:
report_cols = ['Id', 'StatTime', 'Minute', 'Active.1', 'Score1', 'Score2', 'Result1', 'Result2', 'W1', 'WX', 'W2', 'H_prob', 'D_prob', 'A_prob']

In [ ]:
data_df[report_cols].head(100)

Id             StatTime  Minute  Active.1  Score1  Score2  Result1  \
0   6291479  18.02.2023 12:50:44       1         1       0       0        0   
1   6291479  18.02.2023 12:52:04       2         1       0       0        0   
2   6291479  18.02.2023 12:53:25       4         1       0       0        0   
3   6291479  18.02.2023 12:54:58       5         1       0       0        0   
4   6291479  18.02.2023 12:55:58       6         1       0       0        0   
5   6291479  18.02.2023 12:57:05       7         1       0       0        0   
6   6291479  18.02.2023 12:57:50       8         1       0       0        0   
7   6291479  18.02.2023 12:58:43       9         1       0       0        0   
8   6291479  18.02.2023 12:59:35      10         1       0       0        0   
9   6291479  18.02.2023 13:01:02      11         1       0       0        0   
10  6291479  18.02.2023 13:02:04      12         1       0       0        0   
11  6291479  18.02.2023 13:02:45      13         1       0       0        0   
12  6291479  18.02.2023 13:03:46      14         1       0       0        0   
13  6291479  18.02.2023 13:04:47      15         1       0       0        0   
14  6291479  18.02.2023 13:05:47      16         1       0       0        0   
15  6291479  18.02.2023 13:07:55      18         1       0       0        0   
16  6291479  18.02.2023 13:08:44      19         1       0       0        0   
17  6291479  18.02.2023 13:09:54      20         1       0       0        0   
18  6291479  18.02.2023 13:10:40      21         1       0       0        0   
19  6291479  18.02.2023 13:12:00      22         1       0       0        0   
20  6291479  18.02.2023 13:12:46      23         1       0       0        0   
21  6291479  18.02.2023 13:13:57      24         1       0       0        0   
22  6291479  18.02.2023 13:15:04      25         1       0       0        0   
23  6291479  18.02.2023 13:15:59      26         1       0       0        0   
24  6291479  18.02.2023 13:16:44      27         1       0       0        0   
25  6291479  18.02.2023 13:17:49      28         1       0       0        0   
26  6291479  18.02.2023 13:18:07      29         1       0       0        0   
27  6291479  18.02.2023 13:19:55      30         1       0       0        0   
28  6291479  18.02.2023 13:21:03      31         1       0       0        0   
29  6291479  18.02.2023 13:22:02      32         1       0       0        0   
30  6291479  18.02.2023 13:22:41      33         1       0       0        0   
31  6291479  18.02.2023 13:23:43      34         1       0       0        0   
32  6291479  18.02.2023 13:25:01      35         1       0       0        0   
33  6291479  18.02.2023 13:25:29      36         1       0       0        0   
34  6291479  18.02.2023 13:26:22      37         1       0       0        0   
35  6291479  18.02.2023 13:27:43      38         1       0       0        0   
36  6291479  18.02.2023 13:30:04      40         1       0       1        0   
37  6291479  18.02.2023 13:30:37      41         1       0       1        0   
38  6291479  18.02.2023 13:32:05      42         1       0       1        0   
39  6291479  18.02.2023 13:33:04      43         1       0       1        0   
40  6291479  18.02.2023 13:33:40      44         1       0       1        0   
41  6291479  18.02.2023 13:34:47      45         1       0       1        0   
42  6291480  18.02.2023 13:01:06       1         1       0       0        2   
43  6291480  18.02.2023 13:01:57       2         1       0       0        2   
44  6291480  18.02.2023 13:03:02       3         1       0       0        2   
45  6291480  18.02.2023 13:04:00       4         1       0       0        2   
46  6291480  18.02.2023 13:05:06       5         1       0       0        2   
47  6291480  18.02.2023 13:05:57       6         1       0       0        2   
48  6291480  18.02.2023 13:07:02       7         1       0       0        2   
49  6291480  18.02.2023 13:08:00       8         1       0 

In [ ]:
data_df[report_cols].iloc[235500:235510]

Id             StatTime  Minute  Active.1  Score1  Score2  \
235500  6319503  24.02.2023 19:32:49      45         1       1       1   
235501  6518469  12.04.2023 22:59:59       1         0       0       0   
235502  6518469  12.04.2023 23:00:19       2         0       0       0   
235503  6518469  12.04.2023 23:03:08       4         0       0       1   
235504  6518469  12.04.2023 23:03:49       5         0       0       1   
235505  6518469  12.04.2023 23:04:58       6         0       0       1   
235506  6518469  12.04.2023 23:06:05       7         0       0       1   
235507  6518469  12.04.2023 23:06:47       8         0       0       1   
235508  6518469  12.04.2023 23:08:05       9         0       0       1   
235509  6518469  12.04.2023 23:08:52      10         0       0       1   

        Result1  Result2   W1    WX    W2    H_prob    D_prob    A_prob  
235500        1        1  3.4  2.35  2.74  0.254883  0.357064  0.388053  
235501        1        1  0.0  0.00  0.00  0.280020  0.254119  0.465861  
235502        1        1  0.0  0.00  0.00  0.283583  0.260243  0.456173  
235503        1        1  0.0  0.00  0.00  0.110716  0.173150  0.716134  
235504        1        1  0.0  0.00  0.00  0.133310  0.201677  0.665014  
235505        1        1  0.0  0.00  0.00  0.133783  0.209701  0.656516  
235506        1        1  0.0  0.00  0.00  0.135329  0.208147  0.656524  
235507        1        1  0.0  0.00  0.00  0.139308  0.208878  0.651814  
235508        1        1  0.0  0.00  0.00  0.138127  0.205738  0.656135  
235509        1        1  0.0  0.00  0.00  0.150042  0.218555  0.631403

#### Upload to Yandex

In [ ]:
data_df[report_cols].to_csv('./multiclass_probabilities.csv', index = False)

In [ ]:
data_df.to_csv('./multiclass_dataframe.csv', index = False)

In [ ]:
try:
    import yadisk
except:
    !pip install yadisk >> None
    import yadisk
def get_credential2(frmwork = 'yandex token'):
    with open('cred.txt', 'r') as container:
        for line in container:
            if frmwork in line:
                login, psw = line.split(' ')[1], line.split(' ')[2].split('\n')[0]
                return login, psw
_, api_key2 = get_credential2()
y = yadisk.YaDisk(token = api_key2)
print('Token exists: ', y.check_token())

Token exists:  True


In [ ]:
#print(y.mkdir('disk:/sport_prediction/calcio_2021/uploads/20230329'))

In [ ]:
with open('/content/multiclass_probabilities.csv', 'rb') as f:
    y.upload(f, 'disk:/sport_prediction/calcio_2021/uploads/20230504/multiclass_probabilities.csv')

### visualize results

#### assign data

In [ ]:
np.sum((data_df['W1'] > 1) & (data_df['WX'] > 1) & (data_df['W2'] > 1) & (data_df['Active.1'] > 0)), data_df['Active.1'].shape

(1032509, (1224315,))

In [ ]:
y_dict = {'validation':1 - np.sign((data_df['Result1'] - data_df['Result2']).values)}
line_dict = {'validation':data_df[['W1', 'WX', 'W2']].values}
active_rows_dict = {'validation':\
                    (data_df['W1'] > 1) & \
                    (data_df['WX'] > 1) & \
                    (data_df['W2'] > 1) & \
                    (data_df['Active.1'] > 0)
                    }
preds_dict = {'validation':preds}

#### imports

In [ ]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.subplots as sp
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

#### functions

In [ ]:
def calculate_multiclass(probability_2x:np.array, line_2x:np.array):

    probline = probability_2x * line_2x
    best_odd_result = np.argmax(probline, axis = 1)
    best_odd_float = np.take_along_axis(probline, best_odd_result.reshape(-1, 1), axis = 1)
    return {
        'argmax':best_odd_result,
        'float':best_odd_float[:,0],
    }

In [ ]:
def make_filter(hda, preds_int):
    hda_dict = {'home':0, 'draw':1, 'away':2}
    if hda == 'all':
        return preds_int > -1
    else:
        return preds_int == hda_dict[hda]

In [ ]:
def plot_ga_equity_separate(
    sel_best_dict = {'home':1.143, 'draw':1.143, 'away':1.143},
    y_dict = y_dict, line_dict = line_dict, 
    preds_dict = preds_dict, active_rows_dict = active_rows_dict, 
    neptune_model_version = neptune_model_version, data_split = 'validation'):
    
    hda_dict = {'all':{'ltype':'solid', 'colors':'rgb(93, 164, 214)', 'line_width':3}, 
                'home':{'ltype':'dot', 'colors':'rgb(255, 144, 14)', 'line_width':1}, 
                'draw':{'ltype':'dot', 'colors':'rgb(44, 160, 101)', 'line_width':1}, 
                'away':{'ltype':'dot', 'colors':'rgb(255, 65, 54)', 'line_width':1}}
    layout_dict = {}
    data_list = []
    preds_int, preds_float = calculate_multiclass(
        preds_dict[data_split], 
        line_dict[data_split]).values()
    ################
    filter_ga_dict = {}
    for hda in ['home', 'draw', 'away']:
        sfilter = make_filter(hda, preds_int)
        filter_ga_dict[hda] = (sel_best_dict[hda] <= preds_float) & sfilter
    new_ard =  (filter_ga_dict['home'] |  filter_ga_dict['draw'] |  filter_ga_dict['away']) & active_rows_dict[data_split]
    ################
    y_true = (y_dict[data_split][new_ard] == preds_int[new_ard]) * 1
    Line_production = np.take_along_axis(
        line_dict[data_split][new_ard],
        preds_int[new_ard].reshape(-1,1), 
        axis = 1)[:, 0]
    profit_size = (Line_production - 1) / Line_production
    bet_size = Line_production
    mean_bet = np.mean(1/bet_size)
    bet_qty = np.sum(new_ard)
    cumsum_dict = {}
    for hda, value_dict in hda_dict.items():
        if hda != 'all':
            sfilter = make_filter(hda, preds_int[new_ard])
            cumsum_dict[hda] = (y_true * profit_size + (y_true - 1) / bet_size) * sfilter
            y = np.cumsum(cumsum_dict[hda])
            data_list += [
                go.Scatter(
                    y = y, 
                    name = hda, 
                    line = dict(color = value_dict['colors'], width = value_dict['line_width'], dash = value_dict['ltype'])
                            )]
        

    cumsum_dict['all'] = np.cumsum(np.array((cumsum_dict['home'], cumsum_dict['draw'], cumsum_dict['away'])).sum(axis = 0))
    data_list += [
        go.Scatter(
            y = cumsum_dict['all'], 
            name = 'all', 
            line = dict(color = hda_dict['all']['colors'], width = hda_dict['all']['line_width'], dash = hda_dict['all']['ltype'])
                    )]
    title_text = f'Equity Curve {data_split}<br>Model in neptune.ai: FOOT-{neptune_model_version}<br>' + \
        f"ROI: {np.round(cumsum_dict['all'][-1] * 100 / np.sum(1/Line_production), 4)}%" + \
        f' | Bet quantity: {bet_qty}<br>'
    layout_dict.update({
    'width':1200,
    'height':800,
    #'title_x':0.5,
    'title_text':title_text,
    'paper_bgcolor':'rgb(229, 237, 247)',
    'plot_bgcolor':'rgb(229, 237, 247)'
                    })
    layout = go.Layout(**layout_dict)
    return go.Figure(data=data_list, layout=layout)

#### visualization

In [ ]:
fig = plot_ga_equity_separate()
fig.show()

[1.02662898 1.0476772  1.02889136 ... 0.92083545 0.91828773 0.92083545]
49334
17602
59593
